# Capstone Project - Milan, Where open a pizza shop?

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)
* [Bibliopgraphy](#Bibliopgraphy)

## Introduction: Business Problem <a name="introduction"></a>

Pizza is one of the most famous Italian dishes. And there are so many good reasons why! As can see from previous research (i.e. Turrini et.al. 2001, Di Vita et.al. 2016), pizza is an important food for Italian’s diet. And due to the famous of the pizza, almost all the tourist that came to Italy want to taste “The true Italian Pizza”. 

Milan is the second most populated city in Italy, with almost 1,300,000 habitants and have the biggest airport in Italy. Is also, the Italian city with the best public transport and a great transport connection network.  All these, make that Milan offers then a huge market for selling pizza. But, of course, this is not something new for anyone in Italy. 

Never the less, choose the correct place to open a Pizza shop is quite difficult, science there are many variables that can affect the success or failed of a food business (i.e., quality, price, location). Based on the free available information this problem will address this problem in order to have different cluster neighborhood and see the characteristics of the same to define which is the best option to open the pizza shop. 

This project is oriented to help an investment, that will decide in which Milan district open a new pizza shop.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the district (any type of restaurant)
* number of and distance to Pizza Shop in the district, if any
* distance of neighborhood from city center

**Data sources:**

To choose the best place for open a pizza shop we will consider, each district (148) and according to the division that can be found in https://it.wikipedia.org/wiki/Municipi_di_Milano#cite_note-3.
 

Then we will obtain the coordinates of each using MapQuest Open APIs, that offers a free API key to obtain address information based on coordinates or coordinates based on address specification, like the districts https://developer.mapquest.com/documentation/open/.

Then we will obtain the number of pizza shops from Foursquare venues and all the type of restaurants per district. This will allow us to related the number of habitants with the amount of pizza shops and restaurants. Also, to know if the pizza is the venue category that is most repeated in that district or in which category it is. 
All this will allow us to make the cluster of the districts and analyzed which district is more susceptible to the open of a new pizza shop. 


### Districts Candidates

Lets choose search for all the Milan's districts from Wikipedia

In [91]:
#Moldules to be use
import geocoder
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
import folium # map rendering library
from pandas.io.json import json_normalize
from folium import plugins
from folium.plugins import HeatMap
from scipy.interpolate import griddata
import scipy as sp
import scipy.ndimage
import matplotlib.pyplot as plt
import branca
import geojsoncontour
import matplotlib
import utm
from sklearn.cluster import KMeans

In [2]:
source = requests.get("https://it.wikipedia.org/wiki/Municipi_di_Milano#cite_note-3").text
Page= BeautifulSoup(source, "lxml")
print(Page.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="it">
 <head>
  <meta charset="utf-8"/>
  <title>
   Municipi di Milano - Wikipedia
  </title>
  <script>
   document.documentElement.className = document.documentElement.className.replace( /(^|\s)client-nojs(\s|$)/, "$1client-js$2" );
  </script>
  <script>
   (window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Municipi_di_Milano","wgTitle":"Municipi di Milano","wgCurRevisionId":103833354,"wgRevisionId":103833354,"wgArticleId":1099417,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Municipi di Milano"],"wgBreakFrames":false,"wgPageContentLanguage":"it","wgPageContentModel":"wikitext","wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","gennaio","febbraio","marzo","aprile","maggio","giugno","l

In [3]:
Table = Page.find('table',class_="wikitable sortable")

In [4]:
headings = [th.get_text().strip() for th in Table.find("tr").find_all("th")]
headings = np.array(headings)
A=headings.shape
rows = [td.get_text().strip() for td in Table.tbody.find_all("td")]
rows =np.array(rows)
B=rows.shape
print(headings)

['#' 'Denominazione' 'Superficie(km²)' 'Abitanti(31.12.2015)'
 'Densità(ab/km²)' 'Quartieri compresi[4]']


In [5]:
df = pd.DataFrame(np.array(rows).reshape(int(B[0]/A[0]),A[0],), columns=headings)
df.columns = ['Borough','Names','Area_Km2','Population','Pop_Density_hab_km2','Districts']
df.head()

Borough                                              Names Area_Km2  \
0  Municipio 1                                     Centro storico     9,67   
1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...    12,58   
2  Municipio 3                     Città Studi, Lambrate, Venezia    14,23   
3  Municipio 4                                Vittoria, Forlanini    20,95   
4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio    29,87   

  Population Pop_Density_hab_km2  \
0     97.403           10.072,70   
1    159.134           12.649,76   
2    142.939           10.044,91   
3    159.750            7.625,29   
4    124.903            4.181,55   

                                           Districts  
0  Cordusio, Cinque Vie, Carrobbio, Verziere, Pas...  
1  Stazione Centrale, Loreto, Turro, Crescenzago,...  
2  Porta Venezia, Porta Monforte, Casoretto, Rott...  
3  Porta Vittoria, Porta Romana, Cavriano, Quarti...  
4  Porta Vigentina, Porta Lodovica, San Gottardo,...

Now lets convert the number files from Italian format to international format 

In [6]:
df["Area_Km2"] = df["Area_Km2"].str.replace(",",".").astype(float)
df["Population"] = df["Population"].str.replace(".","").astype(int)
df["Pop_Density_hab_km2"] = df["Pop_Density_hab_km2"].str.replace(".","")
df["Pop_Density_hab_km2"] = df["Pop_Density_hab_km2"].str.replace(",",".").astype(float)
df.head()

Borough                                              Names  Area_Km2  \
0  Municipio 1                                     Centro storico      9.67   
1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...     12.58   
2  Municipio 3                     Città Studi, Lambrate, Venezia     14.23   
3  Municipio 4                                Vittoria, Forlanini     20.95   
4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio     29.87   

   Population  Pop_Density_hab_km2  \
0       97403             10072.70   
1      159134             12649.76   
2      142939             10044.91   
3      159750              7625.29   
4      124903              4181.55   

                                           Districts  
0  Cordusio, Cinque Vie, Carrobbio, Verziere, Pas...  
1  Stazione Centrale, Loreto, Turro, Crescenzago,...  
2  Porta Venezia, Porta Monforte, Casoretto, Rott...  
3  Porta Vittoria, Porta Romana, Cavriano, Quarti...  
4  Porta Vigentina, Porta Lodovica, San Gottardo,...

Since the districst are inside the Borough, lets extrac them and verify if there are any duplicated district, and see the final table

In [7]:
df=df['Districts'].str.split(pat = ",",expand=True) \
    .merge(df, left_index = True, right_index = True) \
    .drop(["Districts"], axis = 1) \
    .melt(id_vars = ['Borough','Names','Area_Km2','Population','Pop_Density_hab_km2'], value_name = "Districts")\
    .drop("variable", axis = 1)\
    .dropna()\
    .reset_index()
print(df.shape)
df['Districts']=df['Districts'].str.lstrip(" ")
df=df.drop_duplicates(subset="Districts", keep='first')
print(df.shape)
df.head()

(148, 7)
(148, 7)


index      Borough                                              Names  \
0      0  Municipio 1                                     Centro storico   
1      1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
2      2  Municipio 3                     Città Studi, Lambrate, Venezia   
3      3  Municipio 4                                Vittoria, Forlanini   
4      4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio   

   Area_Km2  Population  Pop_Density_hab_km2          Districts  
0      9.67       97403             10072.70           Cordusio  
1     12.58      159134             12649.76  Stazione Centrale  
2     14.23      142939             10044.91      Porta Venezia  
3     20.95      159750              7625.29     Porta Vittoria  
4     29.87      124903              4181.55    Porta Vigentina

**Obtain the Districts coordinates**

In [8]:
df['Latitude'] = None
df['Longitude'] = None
for i in df.index:
    g = geocoder.mapquest(str(df.Districts[i]+ " (Milano), " +df.Borough[i] +" , Milan, Italy"), key='PpfRVJNdWUEgzuSIzRp2cLPVnAYeeKdW')
    df.at[i, 'Longitude']=g.lng
    df.at[i, 'Latitude']=g.lat
    #print(i, g.lng, g.lat)
df.head()

index      Borough                                              Names  \
0      0  Municipio 1                                     Centro storico   
1      1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
2      2  Municipio 3                     Città Studi, Lambrate, Venezia   
3      3  Municipio 4                                Vittoria, Forlanini   
4      4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio   

   Area_Km2  Population  Pop_Density_hab_km2          Districts Latitude  \
0      9.67       97403             10072.70           Cordusio  45.4649   
1     12.58      159134             12649.76  Stazione Centrale  45.4645   
2     14.23      142939             10044.91      Porta Venezia  45.4759   
3     20.95      159750              7625.29     Porta Vittoria  45.4625   
4     29.87      124903              4181.55    Porta Vigentina  45.4539   

  Longitude  
0   9.18589  
1   9.18644  
2   9.20127  
3   9.19753  
4   9.19604

**Map Visualization**

In [9]:
g = geocoder.mapquest("Milano, Milano, Italia", key='PpfRVJNdWUEgzuSIzRp2cLPVnAYeeKdW')
latitude = g.lat
longitude = g.lng
map_Milan = folium.Map(location=[latitude, longitude], zoom_start=12)
# add markers to map
for lat, lng, label in zip(df.Latitude, df.Longitude, df.Districts):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Milan)  
map_Milan

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting districts of Milan that have low restaurant density, particularly those with low number of pizza shop, and see how many habitants we have per pizza shop.  We will limit our analysis to the Milan districts according, to Wikipedia information.

In first step we have collected the data: All the Milan's districts, their location and their population density, using the Wikipedia information BeautifulSoup, mapquest, pandas and folium. 

Second, we will calculate the population per district, get location and type (category) of every restaurant type (category) of every restaurant per district. We have also identified pizza shop (according to Foursquare categorization).

Third step in our analysis will be calculation and exploration of restaurant density across different districts of Milan, we will use heatmaps to identify a few promising areas with low number of pizza shop and an important number of costumers and focus our attention on those areas.

In finally we will focus on most promising districts and within those create clusters of locations that meet some basic requirements: we will take into consideration locations with less restaurants in radius of 250 meters, and we want locations without Italian restaurants in pizza shops of 500 meters. We will present map of all such locations but also create clusters (using k-means clustering) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Lets see how many Districts we have per Borough

In [10]:
Counts=df['Borough'].value_counts()
Counts.reset_index(name='values')

index  values
0  Municipio 8      22
1  Municipio 5      21
2  Municipio 4      18
3  Municipio 6      18
4  Municipio 9      18
5  Municipio 7      15
6  Municipio 1      15
7  Municipio 2      12
8  Municipio 3       9

We assume that each district has the same size inside each Borough, and according to this we can calculate the population inside each distrisct 

In [11]:
for i in range(len(Counts)):
    df.loc[df['Borough'] ==Counts.index[i], 'Area_Km2']=df.Area_Km2/Counts.values[i]
  # df.loc[df['Borough'] ==Counts.index[i], 'Population']=df.Population/Counts.values[i]
df.Population=df.Pop_Density_hab_km2*df.Area_Km2
df.Population=df.Population.astype(int)
df.head()


index      Borough                                              Names  \
0      0  Municipio 1                                     Centro storico   
1      1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
2      2  Municipio 3                     Città Studi, Lambrate, Venezia   
3      3  Municipio 4                                Vittoria, Forlanini   
4      4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio   

   Area_Km2  Population  Pop_Density_hab_km2          Districts Latitude  \
0  0.644667        6493             10072.70           Cordusio  45.4649   
1  1.048333       13261             12649.76  Stazione Centrale  45.4645   
2  1.581111       15882             10044.91      Porta Venezia  45.4759   
3  1.163889        8874              7625.29     Porta Vittoria  45.4625   
4  1.422381        5947              4181.55    Porta Vigentina  45.4539   

  Longitude  
0   9.18589  
1   9.18644  
2   9.20127  
3   9.19753  
4   9.19604

### Foursquare

We're interested in venues in 'food' category

In [12]:
CLIENT_ID = 'xxx' # your Foursquare ID
CLIENT_SECRET = 'xxx' # your Foursquare Secret
VERSION = '20180605' # Foursquare API versi

In [13]:
LIMIT = 500 # limit of number of venues returned by Foursquare API

radius = 1000 # define radius

search_query='4d4b7105d754a06374d81259' # Food places 

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(str('Get results for: '+ name))
            
        # create the API request URL
        url='https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&categoryId={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            lat, 
            lng, 
            VERSION, 
            search_query, 
            radius, 
            LIMIT)

            
        # make the GET request
        results = requests.get(url).json()["response"]#['groups'][0]['items']
        TOT=len(results['venues'])
        # return only relevant information for each nearby venue
        
        for i in range(TOT):

            if len(results['venues'][i]['categories'])<1:
                results['venues'][i]['categories']=[{'id': 'NON',
                                                     'name': 'NON','pluralName': 'NON',
                                                     'shortName': 'NON', 'icon': {'prefix': '',
                                                                                    'suffix': ''},
                                                     'primary': True}]
                print(results['venues'][i]['categories'][0]['name'], results['venues'][i]['categories'][0]['shortName'])

                
                
        venues_list.append([(
            name, 
            lat, 
            lng, 
            results['venues'][i]['name'], 
            results['venues'][i]['location']['lat'], 
            results['venues'][i]['location']['lng'],  
            results['venues'][i]['categories'][0]['name'],
            results['venues'][i]['categories'][0]['shortName'])
            for i in range(TOT)])
        

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['District', 
                  'District Latitude', 
                  'District Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category',
                  'Venue Short Category',]
    
    return(nearby_venues)

In [14]:
Milan_venues2 = getNearbyVenues(names=df['Districts'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                              )
Milan_venues2.head()

Get results for: Cordusio
Get results for: Stazione Centrale
Get results for: Porta Venezia
Get results for: Porta Vittoria
Get results for: Porta Vigentina
Get results for: Porta Ticinese
Get results for: Porta Magenta
Get results for: Porta Volta
Get results for: Porta Garibaldi
Get results for: Cinque Vie
Get results for: Loreto
Get results for: Porta Monforte
Get results for: Porta Romana
Get results for: Porta Lodovica
Get results for: Porta Genova
Get results for: Quartiere De Angeli - Frua
Get results for: Bullona
Get results for: Porta Nuova
Get results for: Carrobbio
Get results for: Turro
Get results for: Casoretto
Get results for: Cavriano
Get results for: San Gottardo
Get results for: Conchetta
Get results for: San Siro
Get results for: Ghisolfa
Get results for: Centro Direzionale
Get results for: Verziere
Get results for: Crescenzago
Get results for: Rottole
Get results for: Quartiere Forlanini
Get results for: Morivione
Get results for: Moncucco
Get results for: Quartiere

District  District Latitude  District Longitude  \
0  Cordusio           45.46491             9.18589   
1  Cordusio           45.46491             9.18589   
2  Cordusio           45.46491             9.18589   
3  Cordusio           45.46491             9.18589   
4  Cordusio           45.46491             9.18589   

                        Venue  Venue Latitude  Venue Longitude  \
0  Starbucks Reserve Roastery       45.464920         9.186153   
1   Ciacco. Gelato senz'altro       45.463704         9.186796   
2                         KFC       45.464281         9.187572   
3               Panini Durini       45.464299         9.187460   
4      Granaio Caffé e Cucina       45.465692         9.188366   

         Venue Category Venue Short Category  
0           Coffee Shop          Coffee Shop  
1        Ice Cream Shop            Ice Cream  
2  Fast Food Restaurant            Fast Food  
3        Sandwich Place           Sandwiches  
4    Italian Restaurant              Italian

In [15]:
Milan_venues2

District  District Latitude  District Longitude  \
0             Cordusio           45.46491             9.18589   
1             Cordusio           45.46491             9.18589   
2             Cordusio           45.46491             9.18589   
3             Cordusio           45.46491             9.18589   
4             Cordusio           45.46491             9.18589   
5             Cordusio           45.46491             9.18589   
6             Cordusio           45.46491             9.18589   
7             Cordusio           45.46491             9.18589   
8             Cordusio           45.46491             9.18589   
9             Cordusio           45.46491             9.18589   
10            Cordusio           45.46491             9.18589   
11            Cordusio           45.46491             9.18589   
12            Cordusio           45.46491             9.18589   
13            Cordusio           45.46491             9.18589   
14            Cordusio           45.46491             9.18589   
15            Cordusio           45.46491             9.18589   
16            Cordusio           45.46491             9.18589   
17            Cordusio           45.46491             9.18589   
18            Cordusio           45.46491             9.18589   
19            Cordusio           45.46491             9.18589   
20            Cordusio           45.46491             9.18589   
21            Cordusio           45.46491             9.18589   
22            Cordusio           45.46491             9.18589   
23            Cordusio           45.46491             9.18589   
24            Cordusio           45.46491             9.18589   
25            Cordusio           45.46491             9.18589   
26            Cordusio           45.46491             9.18589   
27            Cordusio           45.46491             9.18589   
28            Cordusio           45.46491             9.18589   
29            Cordusio           45.46491             9.18589   
...                ...                ...                 ...   
5411            Trenno           45.44713             9.20154   
5412            Trenno           45.44713             9.20154   
5413            Trenno           45.44713             9.20154   
5414            Trenno           45.44713             9.20154   
5415            Trenno           45.44713             9.20154   
5416            Trenno           45.44713             9.20154   
5417            Trenno           45.44713             9.20154   
5418            Trenno           45.44713             9.20154   
5419            Trenno           45.44713             9.20154   
5420            Trenno           45.44713             9.20154   
5421  Cascina Merlata.           45.48512             9.13752   
5422  Cascina Merlata.           45.48512             9.13752   
5423  Cascina Merlata.           45.48512             9.13752   
5424  Cascina Merlata.           45.48512             9.13752   
5425  Cascina Merlata.           45.48512             9.13752   
5426  Cascina Merlata.           45.48512             9.13752   
5427  Cascina Merlata.           45.48512             9.13752   
5428  Cascina Merlata.           45.48512             9.13752   
5429  Cascina Merlata.           45.48512             9.13752   
5430  Cascina Merlata.           45.48512             9.13752   
5431  Cascina Merlata.           45.48512             9.13752   
5432  Cascina Merlata.           45.48512             9.13752   
5433  Cascina Merlata.           45.48512             9.13752   
5434  Cascina Merlata.           45.48512             9.13752   
5435  Cascina Merlata.           45.48512             9.13752   
5436  Cascina Merlata.           45.48512             9.13752   
5437  Cascina Merlata.           45.48512             9.13752   
5438  Cascina Merlata.           45.48512             9.13752   
5439  Cascina Merlata.           45.48512             9.13752   
5440  Cascina Merlata.           45.48512        

Lest what we found 

In [16]:
print("The total of food places is: "+ str(Milan_venues2.shape[0]))
print("The total of pizza places is: "+str(Milan_venues2[Milan_venues2['Venue Category'].str.contains("Pizza")].shape[0]))
print("The percentage of pizza places is: "+ str(round(Milan_venues2[Milan_venues2['Venue Category'].str.contains("Pizza")].shape[0]/Milan_venues2.shape[0]*100,2)))

The total of food places is: 5441
The total of pizza places is: 683
The percentage of pizza places is: 12.55


In [17]:
print("The total of pizza and italian places is: "+str(Milan_venues2[Milan_venues2['Venue Category'].str.contains("Pizza")].shape[0]+Milan_venues2[Milan_venues2['Venue Category'].str.contains("Italian")].shape[0]))


The total of pizza and italian places is: 1399


Lets see the most common food place category

In [18]:
print(Milan_venues2['Venue Category'].mode())

0    Café
dtype: object


In [76]:
map_Milan2 = folium.Map(location=[latitude, longitude], zoom_start=13)
folium.Marker(location=[latitude, longitude]).add_to(map_Milan2)
a=0
for lng, lat, label in zip(Milan_venues2['Venue Latitude'], Milan_venues2['Venue Longitude'], Milan_venues2['Venue Short Category']):
    label = folium.Popup(label, parse_html=True)
    
    if Milan_venues2['Venue Short Category'][a]== 'Pizza':
        color2='blue'
    else:
        color2='red'
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color=color2,
        fill=True,
        fill_color='color2',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Milan2) 
    a=a+1
map_Milan2


In [20]:
map_Milan4 = folium.Map(location=[latitude, longitude], zoom_start=12)
Res = pd.DataFrame(Milan_venues2, columns= ['Venue Latitude', 'Venue Longitude']).values.tolist()
HeatMap(Res).add_to(map_Milan4)
map_Milan4

Lets see in how many district have at least one pizza shop

In [21]:
Milan_venues2.District[Milan_venues2['Venue Category'].str.contains("Pizza")].nunique()

138

So we have some Districts open for a pizza shop, lets see how many costumers could we have per districts according to the quantity of pizza shops per district

In [22]:
df['Coustumers'] = None
for i in df.index:
    a=df.Districts[i]
    df.at[i, 'Coustumers']=df.Population[i]/(1+sum(Milan_venues2['Venue Category'][Milan_venues2.District==a].str.contains("Pizza")))
df.head()

index      Borough                                              Names  \
0      0  Municipio 1                                     Centro storico   
1      1  Municipio 2  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
2      2  Municipio 3                     Città Studi, Lambrate, Venezia   
3      3  Municipio 4                                Vittoria, Forlanini   
4      4  Municipio 5                Vigentino, Chiaravalle, Gratosoglio   

   Area_Km2  Population  Pop_Density_hab_km2          Districts Latitude  \
0  0.644667        6493             10072.70           Cordusio  45.4649   
1  1.048333       13261             12649.76  Stazione Centrale  45.4645   
2  1.581111       15882             10044.91      Porta Venezia  45.4759   
3  1.163889        8874              7625.29     Porta Vittoria  45.4625   
4  1.422381        5947              4181.55    Porta Vigentina  45.4539   

  Longitude Coustumers  
0   9.18589    590.273  
1   9.18644    1205.55  
2   9.20127     3176.4  
3   9.19753       1479  
4   9.19604    660.778

In [23]:
# The original data
x_orig = np.asarray(df.Longitude.tolist())
y_orig = np.asarray(df.Latitude.tolist())
z_orig = np.asarray(df.Coustumers.tolist())

# Make a grid
x_arr          = np.linspace(np.min(x_orig), np.max(x_orig), 5000)
y_arr          = np.linspace(np.min(y_orig), np.max(y_orig), 5000)
x_mesh, y_mesh = np.meshgrid(x_arr, y_arr)

# Grid the values
z_mesh = griddata((x_orig, y_orig), z_orig, (x_mesh, y_mesh), method='linear')

# Gaussian filter the grid to make it smoother
sigma = [5, 5]
z_mesh = sp.ndimage.filters.gaussian_filter(z_mesh, sigma, mode='constant')

In [24]:
plt.ioff()
# Setup
temp_mean = df.Coustumers.mean()
debug     = False

# Setup colormap
colors = ['green', 'yellow', 'blue', 'red','black']

vmin   = df.Coustumers.min()
vmax   = df.Coustumers.max()
levels = len(colors)
cm     = branca.colormap.LinearColormap(colors, vmin=vmin, vmax=vmax).to_step(levels)

contourf = plt.contourf(x_mesh, y_mesh, z_mesh, levels, alpha=0.5, colors=colors, linestyles='None', vmin=vmin, vmax=vmax);
plt.ioff()
plt.close()

# Convert matplotlib contourf to geojson
geojson = geojsoncontour.contourf_to_geojson(
    contourf=contourf,
    min_angle_deg=3.0,
    ndigits=5,
    stroke_width=1,
    fill_opacity=0.5)
# Set up the folium plot
map_Milan3 = folium.Map(location=[latitude, longitude], zoom_start=13)
# Plot the contour plot on folium
folium.GeoJson(
    geojson,
    style_function=lambda x: {
        'color':     x['properties']['stroke'],
        'weight':    x['properties']['stroke-width'],
        'fillColor': x['properties']['fill'],
        'opacity':   0.6,
    }).add_to(map_Milan3)
map_Milan3.add_child(cm)


### Lambrate

Lets focus in the area of Lambrate wich have an important train station and a lot of people living there, defining a new area

In [25]:
g = geocoder.mapquest("Rimembranze di Lambrate, Milano, Italia", key='xxx')
latitude2 = g.lat
longitude2 = g.lng
map_Lambrate = folium.Map(location=[latitude2, longitude2], zoom_start=16.5)
Data=Milan_venues2[Milan_venues2['Venue Category'].str.contains("Pizza")].reset_index()
Res = pd.DataFrame(Data, columns= ['Venue Latitude', 'Venue Longitude']).values.tolist()
HeatMap(Res).add_to(map_Lambrate)
map_Lambrate

We will get more information about this are:


In [48]:
LIMIT = 100000 # limit of number of venues returned by Foursquare API
radius = 2000 # define radius

name="Rimembranze di Lambrate, Milano, Italia"
lat=latitude2
lng=longitude2

url='https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&categoryId={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    lat, 
    lng, 
    VERSION, 
    search_query, 
    radius, 
    LIMIT)

            
# make the GET request
results = requests.get(url).json()["response"]#['groups'][0]['items']
TOT=len(results['venues'])
# return only relevant information for each nearby venue

venues_list=[]
venues_list.append([(
    name, 
    lat, 
    lng, 
    results['venues'][i]['name'], 
    results['venues'][i]['location']['lat'], 
    results['venues'][i]['location']['lng'],  
    results['venues'][i]['categories'][0]['name'],
    results['venues'][i]['categories'][0]['shortName'])
    for i in range(TOT)])
        

Lambrate_venues2 = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
Lambrate_venues2.columns = ['District', 
                            'District Latitude', 
                            'District Longitude', 
                            'Venue', 
                            'Venue Latitude', 
                            'Venue Longitude', 
                            'Venue Category',
                            'Venue Short Category',]
Lambrate_venues2.head()

District  District Latitude  \
0  Rimembranze di Lambrate, Milano, Italia           45.48246   
1  Rimembranze di Lambrate, Milano, Italia           45.48246   
2  Rimembranze di Lambrate, Milano, Italia           45.48246   
3  Rimembranze di Lambrate, Milano, Italia           45.48246   
4  Rimembranze di Lambrate, Milano, Italia           45.48246   

   District Longitude                              Venue  Venue Latitude  \
0             9.24042                     La Cappelletta       45.484640   
1             9.24042                            Logotel       45.484547   
2             9.24042  MAG - Mastri Artigiani del Gelato       45.481940   
3             9.24042                   le nove scodelle       45.487478   
4             9.24042                          Mens@Sana       45.483386   

   Venue Longitude                 Venue Category Venue Short Category  
0         9.242290                     Restaurant           Restaurant  
1         9.244629                         Office               Office  
2         9.221057                 Ice Cream Shop            Ice Cream  
3         9.217119            Szechuan Restaurant             Szechuan  
4         9.229958  Vegetarian / Vegan Restaurant   Vegetarian / Vegan

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart). For this wee need to change our coordinate system to UTM, so lets start with the Lambrate venues

In [49]:
Lambrate_venues2['District_X']=None
Lambrate_venues2['District_y']=None
Lambrate_venues2['Venue_X']=None
Lambrate_venues2['Venue_Y']=None

for i in range(TOT):
    UTM_DIST=utm.from_latlon(Lambrate_venues2['District Latitude'][i], Lambrate_venues2['District Longitude'][i])
    UTM_VENUE=utm.from_latlon(Lambrate_venues2['Venue Latitude'][i], Lambrate_venues2['Venue Longitude'][i])
    Lambrate_venues2.at[i, 'District_X']=UTM_DIST[0]
    Lambrate_venues2.at[i, 'District_y']=UTM_DIST[1]
    Lambrate_venues2.at[i, 'Venue_X']=UTM_VENUE[0]
    Lambrate_venues2.at[i, 'Venue_Y']=UTM_VENUE[1]
Lambrate_venues2.head()

District  District Latitude  \
0  Rimembranze di Lambrate, Milano, Italia           45.48246   
1  Rimembranze di Lambrate, Milano, Italia           45.48246   
2  Rimembranze di Lambrate, Milano, Italia           45.48246   
3  Rimembranze di Lambrate, Milano, Italia           45.48246   
4  Rimembranze di Lambrate, Milano, Italia           45.48246   

   District Longitude                              Venue  Venue Latitude  \
0             9.24042                     La Cappelletta       45.484640   
1             9.24042                            Logotel       45.484547   
2             9.24042  MAG - Mastri Artigiani del Gelato       45.481940   
3             9.24042                   le nove scodelle       45.487478   
4             9.24042                          Mens@Sana       45.483386   

   Venue Longitude                 Venue Category Venue Short Category  \
0         9.242290                     Restaurant           Restaurant   
1         9.244629                         Office               Office   
2         9.221057                 Ice Cream Shop            Ice Cream   
3         9.217119            Szechuan Restaurant             Szechuan   
4         9.229958  Vegetarian / Vegan Restaurant   Vegetarian / Vegan   

  District_X   District_y Venue_X      Venue_Y  
0     518789  5.03658e+06  518934  5.03682e+06  
1     518789  5.03658e+06  519117  5.03681e+06  
2     518789  5.03658e+06  517276  5.03651e+06  
3     518789  5.03658e+06  516967  5.03713e+06  
4     518789  5.03658e+06  517971  5.03668e+06

In [50]:
UTM=utm.from_latlon(latitude2, longitude2)
xc=UTM[0]
yc=UTM[1]
UTM

(518789.07571010804, 5036575.973065916, 32, 'T')

In [51]:
Lambrate_venues2[Lambrate_venues2['Venue Short Category']=='Pizza']

District  District Latitude  \
24  Rimembranze di Lambrate, Milano, Italia           45.48246   
31  Rimembranze di Lambrate, Milano, Italia           45.48246   
36  Rimembranze di Lambrate, Milano, Italia           45.48246   
38  Rimembranze di Lambrate, Milano, Italia           45.48246   
41  Rimembranze di Lambrate, Milano, Italia           45.48246   
42  Rimembranze di Lambrate, Milano, Italia           45.48246   
44  Rimembranze di Lambrate, Milano, Italia           45.48246   

    District Longitude                   Venue  Venue Latitude  \
24             9.24042          Kebap Pizza.it       45.483186   
31             9.24042       Pizzeria Spontini       45.482009   
36             9.24042           'A Tarantella       45.490889   
38             9.24042              La Cuccuma       45.482123   
41             9.24042          Piccola Ischia       45.481748   
42             9.24042  Pizzeria Piccolo Borgo       45.482743   
44             9.24042          Piccola Ischia       45.477781   

    Venue Longitude Venue Category Venue Short Category District_X  \
24         9.231525    Pizza Place                Pizza     518789   
31         9.213112    Pizza Place                Pizza     518789   
36         9.233899    Pizza Place                Pizza     518789   
38         9.228962    Pizza Place                Pizza     518789   
41         9.217081    Pizza Place                Pizza     518789   
42         9.230598    Pizza Place                Pizza     518789   
44         9.211707    Pizza Place                Pizza     518789   

     District_y Venue_X      Venue_Y  
24  5.03658e+06  518094  5.03665e+06  
31  5.03658e+06  516655  5.03652e+06  
36  5.03658e+06  518277  5.03751e+06  
38  5.03658e+06  517894  5.03654e+06  
41  5.03658e+06  516965  5.03649e+06  
42  5.03658e+06  518021  5.03661e+06  
44  5.03658e+06  516546  5.03605e+06

In [52]:
k = np.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
LAM_y_min = yc - 500
LAM_x_min = xc - 500

LAM_latitudes = []
LAM_longitudes = []
LAM_xs = []
LAM_ys = []

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return np.sqrt(dx*dx + dy*dy)

for i in range(0, int(51/k)):
    y = LAM_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = LAM_x_min + j * x_step + x_offset
        d = calc_xy_distance(xc, yc, x, y)
        if (d <= 501):
            lat, lon = utm.to_latlon(x, y, UTM[2], UTM[3])
            LAM_latitudes.append(lat)
            LAM_longitudes.append(lon)
            LAM_xs.append(x)
            LAM_ys.append(y)

print(len(LAM_longitudes), 'candidate centers generated.')

90 candidate centers generated.


Now let's calculate two most important things for each location candidate: number of restaurants in vicinity (we'll use radius of 250 meters) and distance to closest Pizza shop.

In [53]:
def count_restaurants_nearby(x, y, Lambrate_venues2, radius=250):    
    count = 0
    for i in Lambrate_venues2.index:
        res_x = Lambrate_venues2['Venue_X'][i]; res_y = Lambrate_venues2['Venue_Y'][i]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, Lambrate_venues2):
    d_min = 100000
    for i in Lambrate_venues2.index:
        res_x = Lambrate_venues2['Venue_X'][i]; res_y = Lambrate_venues2['Venue_Y'][i]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

LAM_restaurant_counts = []
LAM_Pizza_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(LAM_xs, LAM_ys):
    count = count_restaurants_nearby(x, y, Lambrate_venues2, radius=250)
    LAM_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, Lambrate_venues2[Lambrate_venues2['Venue Short Category']=='Pizza'])
    LAM_Pizza_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [65]:
# Let's put this into dataframe
LAM_locations = pd.DataFrame({'Latitude':LAM_latitudes,
                                 'Longitude':LAM_longitudes,
                                 'X':LAM_xs,
                                 'Y':LAM_ys,
                                 'Restaurants nearby':LAM_restaurant_counts,
                                 'Distance to Pizza Shop':LAM_Pizza_distances})

LAM_locations.head()

Latitude  Longitude             X             Y  Restaurants nearby  \
0  45.478744   9.237845  518589.07571  5.036163e+06                   0   
1  45.478742   9.239125  518689.07571  5.036163e+06                   0   
2  45.478739   9.240404  518789.07571  5.036163e+06                   0   
3  45.478736   9.241684  518889.07571  5.036163e+06                   0   
4  45.478734   9.242963  518989.07571  5.036163e+06                   0   

   Distance to Pizza Shop  
0              698.199490  
1              772.369418  
2              851.837136  
3              935.253171  
4             1021.650862

Let us now filter those locations: we're interested only in locations with no more than two food places in radius of 250 meters, and no Pizza Shop in radius of 300 meters.

In [86]:
good_res_count = np.array((LAM_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_pizza_distance = np.array(LAM_locations['Distance to Pizza Shop']>=500)
print('Locations with no Pizza Shops within 500m:', good_pizza_distance.sum())

good_locations = np.logical_and(good_res_count, good_pizza_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = LAM_locations[good_locations]

Locations with no more than two restaurants nearby: 90
Locations with no Pizza Shops within 500m: 74
Locations with both conditions met: 74


Let's see how this looks on a map.

In [87]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_Lambrate = folium.Map(location=[latitude2, longitude2], zoom_start=16)
#folium.TileLayer('cartodbpositron').add_to(map_Lambrate)
#HeatMap(restaurant_latlons).add_to(map_Lambrate)
folium.Circle([latitude2, longitude2], radius=500, color='white', fill=True, fill_opacity=0.6).add_to(map_Lambrate)
for lat, lon, label in zip(good_latitudes, good_longitudes, (df_good_locations['Longitude'].index)):
    label=str(label)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lon], radius=2, popup=label, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Lambrate) 
    

    
map_Lambrate

We see that some of these places shoud not be like those over the train rails, so we will clean it a bit more


In [88]:
DELETE=1, 0, 2,6,7,8,16,25,34,44,63,72,79,46,12,53,62,71,72,79

In [89]:
for i in range(len(DELETE)):
    try:
        df_good_locations.drop(DELETE[i],axis=0,inplace=True)
    except :
        pass
            

C:\Users\dubon\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [90]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_Lambrate = folium.Map(location=[latitude2, longitude2], zoom_start=16)
folium.Circle([latitude2, longitude2], radius=500, color='white', fill=True, fill_opacity=0.6).add_to(map_Lambrate)
for lat, lon, label in zip(good_latitudes, good_longitudes, (df_good_locations['Longitude'].index)):
    label=str(label)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lon], radius=2, popup=label, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Lambrate) 
    

    
map_Lambrate

In [84]:
number_of_clusters = 12

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [utm.to_latlon(cc[0], cc[1], UTM[2], UTM[3]) for cc in kmeans.cluster_centers_]

In [85]:
map_Lambrate = folium.Map(location=[latitude2, longitude2], zoom_start=16)
folium.Circle([latitude2, longitude2], radius=500, color='white', fill=True, fill_opacity=0.6).add_to(map_Lambrate)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=10, color='green', fill=True, fill_opacity=0.25).add_to(map_Lambrate) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Lambrate)
map_Lambrate

Finally, let get the addresses which can be presented to stakeholders.

In [74]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lat, lon in cluster_centers:
    addr = geocoder.mapquest([lat, lon], method='reverse', key='xxx').json
    addr=str(addr['address']+ ' '+addr['city']+ ' '+addr['country'])
    candidate_area_addresses.append(addr)    
    A = utm.from_latlon(lat, lon)
    x=A[0]
    y=A[1]
    d = calc_xy_distance(x, y, xc, yc)
    print('{}{} => {:.1f}m from Rimembranze di Lambrate'.format(addr, ' '*(50-len(addr)), d/1))

Addresses of centers of areas recommended for further analysis

Via Carlo Bertolazzi Milan IT                      => 127.1m from Rimembranze di Lambrate
Via Conte Rosso Milan IT                           => 167.8m from Rimembranze di Lambrate
Via privata Giovanni Ventura Milan IT              => 372.2m from Rimembranze di Lambrate
Via dei Canzi Milan IT                             => 340.0m from Rimembranze di Lambrate
Via Carlo Valvassori Peroni Milan IT               => 407.7m from Rimembranze di Lambrate
Via Riccardo Pitteri Milan IT                      => 382.2m from Rimembranze di Lambrate
Via Tommaso Pini Milan IT                          => 388.0m from Rimembranze di Lambrate
Via privata Gaetano Sbodio Milan IT                => 400.0m from Rimembranze di Lambrate
Via Rombon Milan IT                                => 401.7m from Rimembranze di Lambrate
Via Pietro Andrea Saccardo Milan IT                => 137.7m from Rimembranze di Lambrate
Piazza Enrico Bottini Milan IT      

This concludes our analysis. We have created 12 addresses representing centers of zones containing locations with low number of restaurants and no pizza shop nearby. 

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of pizza shops in Milan's districts, there are pockets of low pizza shop density. We focused our attention to Lambrate area. Our attention focused to this area due to the low density of pizza shops and the hihg density of potential coustumers. 

After directing our attention to this more narrow area of interest we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with a Pizza Shop  closer than 500m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 12 zones containing largest number of potential new Pizza Shop locations based on the district population, number of and distance to existing venues - both restaurants in general and Pizza Shop particularly. This, of course, does not imply that those zones are actually optimal locations for a new Pizza Shop! Purpose of this analysis was to only provide info on areas in Milan not crowded with existing restaurants (particularly Pizza Shops) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Berlin areas close to center with low number of restaurants (particularly Pizza Shops) in order to aid stakeholders in narrowing down the search for optimal location for a new Pizza Shop. First we obtained the districts and population from Milan city, after that we get the coorinates of each district, then, by calculating restaurant density distribution from Foursquare data and correlated to the population of each district we choose Lambrate area. Then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.

## Bibliography <a name="Bibliography"></a>

G. Di Vita, G. De Salvo, S. Bracco, G. Gulisano, M. D’Amico. Future Market of Pizza: Which Attributes Do They Matter?, Agris on-line Papers in Economics and Informatics, Volume VIII, Number 4, pp59-71 2016 https://www.researchgate.net/publication/311966640_Future_Market_of_Pizza_Which_Attributes_Do_They_Matter


A. Turrini, A. Saba, D. Perrone2, E. Cialfa and A. D'Amicis. Original Communication Food consumption patterns in Italy: the INN-CA Study 1994 – 1996. European Journal of Clinical Nutrition (2001) 55, 571-588 https://dietistica.campusnet.unito.it/didattica/att/c8b7.3449.file.pdf
